### Imports

In [1]:
import data_gen as gen
from statistics import mean
from typing import List
from math import sqrt, log, pow, inf, exp

In [2]:
budget = 50000
website_list = ["111","112","113","121","122","123"]
data = gen.generate_data(budget, website_list, 0.01, 0.3, 0.03)
data

{'111': <data_gen.Website at 0x7fb5621c0d30>,
 '112': <data_gen.Website at 0x7fb5621ecf40>,
 '113': <data_gen.Website at 0x7fb5621ecd30>,
 '121': <data_gen.Website at 0x7fb5621ec5e0>,
 '122': <data_gen.Website at 0x7fb5621ecdc0>,
 '123': <data_gen.Website at 0x7fb5621ecbb0>}

Checking value for a

In [3]:
def calc_a(data, accuracy, budget, m): 
    ### Computes upper bound on a
 
    num_arms = len(data.keys())
    mu_k = []

    for website in data.keys():
        mu_k.append(mean(data[website].realisations))

    mu_k.sort(reverse=True)

    delta_k = []
    for k, mu in enumerate(mu_k):
        if k <= m:
            delta_k.append(mu-mu_k[m+1])
        else:
            delta_k.append(mu_k[m]-mu)

    H = 0
    for delta_i in delta_k:
        H += 1/( (max(0.5*(delta_i + accuracy), accuracy))**2 )

    a = (budget - num_arms) / 4*H
    a = round(a,3)
    return a

In [4]:
budget = 5000
website_list = ["111","112","113","121","122","123","131","132","133"]
a_list = []
num_opt_arms = 3
acc = 0.05
for i in range(6):
    data = gen.generate_data(budget, website_list, 0.01, 0.3, 0.03)
    a_list.append(calc_a(data, 0.05, budget, num_opt_arms))

round(mean(a_list))

4239140

### Algorithms

#### Helper functions

In [5]:
def calc_beta(arm, a):
    return sqrt(a/arm.num)

In [6]:
def get_max_key(input_dict,keys):
    new_dict = dict()
    for item in keys:
        new_dict[item] = input_dict[item]
    return max(new_dict, key=new_dict.get)


def get_min_key(input_dict, keys):
    new_dict = dict()
    for item in keys:
        new_dict[item] = input_dict[item]
    return min(new_dict, key=new_dict.get)


In [12]:
def select_arm(current_arms, m, a):   
    current_arms = [data[arm_name] for arm_name in data.keys()]

    ukt_dict = dict()
    lkt_dict = dict()
    bkt_dict = dict()
    beta_dict = dict()
    # Compute Uk(t) and Lk(t) for each arm",
    for k in current_arms:
        beta_dict[k] = calc_beta(k, a)
        ukt = k.last_average + beta_dict[k]
        lkt = k.last_average - beta_dict[k]
        ukt_dict[k] = ukt
        lkt_dict[k] = lkt
    # Compute Bk(t) for each arm",
    for k in current_arms:
        ukt_dict_subset = ukt_dict.copy()
        ukt_dict_subset.pop(k)
        # Find max Ukt
        ukt_subset_sorted = dict(
            sorted(ukt_dict_subset.items(), key=lambda item: item[1]))
        max_ukt = list(ukt_subset_sorted.keys())[-m]
        bkt = ukt_dict[max_ukt] - lkt_dict[k]
        bkt_dict[k] = bkt

    # Identify the set of m arms J(t)\n",
    bkt_dict_sorted = dict(sorted(bkt_dict.items(), key=lambda item: item[1]))
    Jt = set(list(bkt_dict_sorted.keys())[:m])

    # Identify arm with minimum lower bound in J(t)\n",
    lowest = inf
    contenders = []
    for arm in Jt:
        if lkt_dict[arm] <= lowest:
            contenders.append(arm)
    if len(contenders) > 1:
        lower = get_min_key(beta_dict, contenders)
    else:
        lower = contenders[0]
    # Identify arm with maximum upper bound *not* in J(t)\n",
    not_in_jt = list(set(ukt_dict.keys()) - Jt)
    highest = -inf
    contenders = []
    for arm in not_in_jt:
        if ukt_dict[arm] >= highest:
            contenders.append(arm)
    if len(contenders) > 1:
        upper = get_max_key(beta_dict, contenders)
    else:
        upper = contenders[0]
    # Identify and pull arm I(t)
    keyz = [lower, upper]
    It = get_max_key(beta_dict, keyz)
    It.pull()

    return Jt, bkt_dict


#### UGabEB

###### UGabE Budget implementation

In [18]:
def UGapEb(data, m, budget, a):
    '''
    Inputs:
    data: (dict) website name as key and website object as value
    m: (Int) number of arms
    budget: (Int) number of iterations (i.e. number of visitor to the website)
    a: (float) exploration parameter (0.5 is always a good choice)

    Outputs:
    website objects (i.e. the optimal arms)
    '''
    K = len(data)
    ## Initialise
    for arm_name in data.keys():
        data[arm_name].pull()
    ## Main loop
    Jt = ''
    bkt_dict = ''
    t = 0
    for t in range(K+1,budget):
        current_arms = [data[arm_name] for arm_name in data.keys()]
        Jt, bkt_dict = select_arm(current_arms, m, a)

    return Jt


budget = 50000
website_list = ["111", "112", "113", "122", "123"]
data = gen.generate_data(budget, website_list, 0.01, 0.3, 0.03)
best = UGapEb(data, 3, 10000, 3063246)

for website in data.keys():
    print(f'{data[website].name}: p={round(data[website].p, 3)}')
print()
for website in best:
    print(
        f'website: {website.name}, num: {website.num}, average: {website.average}, true: {website.p}')



111: p=0.648
112: p=0.631
113: p=0.643
122: p=0.641
123: p=0.642

website: 123, num: 2002, average: 0.6708291708291708, true: 0.6416954427844298
website: 111, num: 1996, average: 0.6623246492985972, true: 0.6479009972447829
website: 122, num: 2001, average: 0.6371814092953523, true: 0.6414976576024989


In [4]:
budget = 50000
website_list = ["111", "112", "113", "122", "123"]
data = gen.generate_data(budget, website_list, 0.1, 0.3, 0.01)
arms = [data[arm_name] for arm_name in data.keys()]
print(sum(arms[0].realisations))
print(sum(arms[1].realisations))
print(sum(arms[2].realisations))
print(sum(arms[3].realisations))
print(sum(arms[4].realisations))


31784
34276
32390
33787
32568


#### UGapEc

In [26]:
a = 4206412
c = 0.5
K = len(data)
t = 1
delta = (4*K*(t-1)**3) / exp(a/c) 

OverflowError: math range error

In [43]:
def UGapEc(data, e, m, delta, c):
    '''
    Inputs:
    data: (dict) website name as key and website object as value
    e: (float) accuracy parameter
    m: (Int) number of optimal arms
    delta: (float) confidence level
    c: (float) exploration parameter (0.5 is always a good choice)

    Outputs:
    Set of website objects (i.e. the optimal arms)
    '''
    K = len(data)
    
    ## Initialise
    for arm_name in data.keys():
        data[arm_name].pull()

    ## Main loop
    Jt = ''
    Bkt_dict = ''
    t = K + 1

    stopping_criteria = True
    while (stopping_criteria):
        current_arms = [data[arm_name] for arm_name in data.keys()]

        a = c * log((4*K*(t**3))/delta)
        Jt, Bkt_dict = select_arm(current_arms, m, a)

        key = get_max_key(Bkt_dict, Jt)
        t += 1
        if (Bkt_dict[key] <= e):
            stopping_criteria = False
    return Jt

In [44]:
budget = 50000
website_list = ["111", "112", "113", "122", "123"]
data = gen.generate_data(budget, website_list, 0.01, 0.3, 0.03)
print("Generated data: ")
for website in data.keys():
    print(f'{data[website].name}: p={round(data[website].p, 3)}')

print("Results: ")
optimal_arms = UGapEc(data, e=0.05, m=3, delta=0.0000001, c=0.5)#UGapEb(data, 3, budget=10000, a=4206412)

for website in optimal_arms:
    print(
        f'website: {website.name}, num: {website.num}, average: {website.average}, true: {website.p}')

Generated data: 
111: p=0.642
112: p=0.615
113: p=0.612
122: p=0.715
123: p=0.621
Results: 
12.244553166098237
3.499221794356316
3.499221794356316
3.499221794356316
3.499221794356316
3.499221794356316
6.998443588712632
12.475779185839125
3.5321069046447513
2.4975767441501295
3.5321069046447513
3.5321069046447513
3.5321069046447513
7.064213809289503
12.676076274775909
3.5603477744141667
2.5175460546706896
3.5603477744141667
3.5603477744141667
2.5175460546706896
7.077893829084856
12.852750828260485
3.5850733365247196
2.5350296673077106
2.5350296673077106
3.5850733365247196
2.5350296673077106
6.070059334615421
13.010791601747224
2.5505677408909593
2.5505677408909593
2.5505677408909593
3.607047490919301
2.5505677408909593
5.101135481781919
13.15375687145371
2.56454253927028
2.56454253927028
2.56454253927028
2.56454253927028
2.56454253927028
5.12908507854056
13.284273936938156
2.5772343642884086
2.5772343642884086
2.1043030466909274
2.5772343642884086
2.5772343642884086
4.681537410979336
13

KeyboardInterrupt: 

In [38]:
delta = 0.9
c = 0.5
optimal_arms = UGapEb(data, 0.6, 3, delta, c)
for arm in optimal_arms:
    print(arm.name)

TypeError: UGapEb() takes 4 positional arguments but 5 were given

#### Unified UGapE

In [28]:
def UGapE(data, accuracy, budget, confidence, m, c):
    K = len(data)

    ## Initialise
    for arm_name in data.keys():
        data[arm_name].pull()

    ## Main loop
    Jt = ''
    Bkt_dict = ''
    reason = ''
    t = K + 1
    budget -= K
    stopping_criteria = True
    while (stopping_criteria):
        budget -= 1
        current_arms = [data[arm_name] for arm_name in data.keys()]
        
        a = c * log((4*K*(t**3))/confidence)
        Jt, Bkt_dict = select_arm(current_arms, m, a)

        key = get_min_key(Bkt_dict, Jt)
        t += 1
        if (Bkt_dict[key] < accuracy):
            stopping_criteria = False
            reason = 'Terminated because specified accuracy has been satisfied'
        elif budget == 0:
            stopping_criteria = False
            reason = 'Terminated because budget is exhausted'
    return Jt, reason
    

#### Testing

In [29]:
budget = 100000
website_list = ["111","112","113","121","122","123","131","132","133"]
data = gen.generate_data(budget, website_list, 0.01, 0.3, 0.03)
print("Generated data: ")
for website in data.keys():
    print(f'{data[website].name}: p={round(data[website].p, 3)}')

Generated data: 
111: p=0.586
112: p=0.591
113: p=0.553
121: p=0.605
122: p=0.575
123: p=0.567
131: p=0.584
132: p=0.596
133: p=0.568


In [30]:
print("Results: ")
optimal_arms, reason = UGapE(data, accuracy=0.05, budget=budget, m=3, confidence=0.01, c=0.5)#UGapEb(data, 3, budget=10000, a=4206412)

print(reason)
for website in optimal_arms:
    print(
        f'website: {website.name}, num: {website.num}, average: {website.average}, true: {website.p}')


Results: 
Terminated because budget is exhausted
website: 121, num: 3661, average: 0.5938268232723299, true: 0.6048536615601285
website: 132, num: 13305, average: 0.6015783540022548, true: 0.5958430824773396
website: 112, num: 3210, average: 0.5990654205607476, true: 0.5913443259921617
